# Mean Teacher Bert Assessment



# Requirement Installation 

In [ ]:
#installing requirements
!pip install tensorflow_text
!pip install textattack
!pip install sentence_transformers

     |████████████████████████████████| 4.9 MB 8.8 MB/s 
     |████████████████████████████████| 373 kB 7.3 MB/s 
     |████████████████████████████████| 3.1 MB 83.2 MB/s 
     |████████████████████████████████| 59 kB 7.6 MB/s 
     |████████████████████████████████| 769 kB 62.0 MB/s 
     |████████████████████████████████| 69 kB 9.4 MB/s 
     |████████████████████████████████| 298 kB 79.4 MB/s 
     |████████████████████████████████| 101 kB 14.3 MB/s 
     |████████████████████████████████| 322 kB 94.2 MB/s 
     |████████████████████████████████| 895 kB 55.6 MB/s 
     |████████████████████████████████| 3.3 MB 54.2 MB/s 
     |████████████████████████████████| 61 kB 538 kB/s 
     |████████████████████████████████| 596 kB 65.5 MB/s 
     |████████████████████████████████| 1.1 MB 52.6 MB/s 
     |████████████████████████████████| 243 kB 89.2 MB/s 
     |████████████████████████████████| 298 kB 96.6 MB/s 
     |████████████████████████████████| 290 kB 92.5 MB/s 
     |████████████████


# Importing and Declaration

In [ ]:
import os 
os.chdir('/content/drive/MyDrive/Master Thesis/Mean-Teacher-BERT-Robustness-Assessment/')

In [ ]:
# importing libraries 
import os 
import datetime

import pandas as pd 
import numpy as np
import tensorflow as tf

from ipywidgets import *
from IPython.display import display


from Utils.utils import label_to_int, dataset_split, convert_to_category, create_tokenizer, data_tokenization
from Utils.data_loader import data_loader
from Bert.bert_model import bert_model



from MeanTeacher.train_mean_teacher import train_mean_teacher

from sklearn.metrics import classification_report

import random 
random.seed(42)

## Data Related Questionaire

In [ ]:
data_name=widgets.Dropdown(options=['codalab','IMDB' ],value='codalab',description='DATA:',disabled=False,) 
pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='distilbert-base-uncased',description='Pretrained Model:',disabled=False,)
widgets.HBox([data_name, pretrained_weights])

### Data specific detail

In [ ]:
'''
NOT required now as previous cell does the job. So disabling boxes
'''
# Details related to the dataset
# columns names 
feature_col=widgets.Text(value='tweet',placeholder='Enter Feature Col Name',description='Feature Column:',disabled=False)
target_col=widgets.Text(value='label',placeholder='Enter Target Col Name',description='Target Column:',disabled=False) 
aug_col=widgets.Text(value='aug_tweet',placeholder='Enter Augmented data Col Name',description='Augment Column:',disabled=False)   

#pretrained model details
 # widgets.HBox([feature_col,target_col,aug_col,pretrained_weights])

In [ ]:
#details of the class
class_1=widgets.Text(value='real',placeholder='Enter class name 1',description='class 1:',disabled=False)
class_2=widgets.Text(value='fake',placeholder='Enter class name 2',description='class 2:',disabled=False) 
tf.print("Class 1 label would be 0. \n")
# widgets.HBox([class_1,class_2])

Class 1 label would be 0. 



In [ ]:
# #Data location 
Data_loc=widgets.Text(value='Data/codalab/',placeholder='Enter Data location ',description=' Data Location Column:',disabled=False)   
# widgets.HBox([Data_loc])

In [ ]:
'''
Adjusting feature as per data 
'''

if data_name.value=='codalab':
    feature_col.value='tweet'
    target_col.value='label'
    aug_col.value='aug_tweet'
    class_1.value='real'
    class_2.value='fake'
    Data_loc.value= 'Data/codalab/'
elif data_name.value=='IMDB':
    feature_col.value='review'
    target_col.value='sentiment'
    aug_col.value='aug_tweet'
    class_1.value='positive'
    class_2.value='negative'
    Data_loc.value= 'Data/IMDB/'



## Hyperparameter selections

In [ ]:
# Parameter declaration 
max_len=widgets.BoundedIntText(value=100,min=10,max=512,step=10,description='Max Length:',disabled=False,)

learning_rate= widgets.Dropdown(options=[2e-5, 1e-5, 1e-3],value=2e-5,description='Learning Rate:',disabled=False,)

epochs= widgets.Dropdown(options=[3, 4, 5,6],value=3,description='Epochs:',disabled=False,)

batch_size= widgets.Dropdown(options=[4, 5,6,7,8],value=4,description='Batch Size:',disabled=False,)

#for mean teacher model
alpha= widgets.BoundedFloatText(value=0.999,min=0.90,max=0.999,step=0.0001,description='Alpha:',disabled=False, readout_format='.3f')
ratio= widgets.BoundedFloatText(value=0.5,min=0.1,max=0.9,step=0.1,description='Ratio:',disabled=False, readout_format='.2f')
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,)

tf.print('\n Max Length: Length of the article')
display(max_len)
tf.print('\n Learning rate: Learning rate for training the model')
display(learning_rate)
tf.print('\n Epochs')
display(epochs)
tf.print('\n batch_size')
display(batch_size)
tf.print('\n Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.')
display(alpha)
tf.print("\n Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.")
display(ratio)

# widgets.HBox([max_len, learning_rate, epochs, batch_size,alpha,ratio])


 Max Length: Length of the article


BoundedIntText(value=100, description='Max Length:', max=512, min=10, step=10)


 Learning rate: Learning rate for training the model


Dropdown(description='Learning Rate:', options=(2e-05, 1e-05, 0.001), value=2e-05)


 Epochs


...

Dropdown(description='Batch Size:', options=(4, 5, 6, 7, 8), value=4)


 Alpha: Parameter related to Mean teacher model, its the proportion of student weight that teacher model will get each step.


BoundedFloatText(value=0.999, description='Alpha:', max=0.999, min=0.9, step=0.0001)


 Ratio: Parameter related to Mean Teacher model, that manage the proportion of classification cost and consistency cost in calculating overall cost.


BoundedFloatText(value=0.5, description='Ratio:', max=0.9, min=0.1, step=0.1)

# Reading dataset

In [ ]:
df_train,df_test,df_aug_unlabel= data_loader(Data_loc.value,target_col.value,aug_col.value,class_1.value)

In [ ]:
len(df_train),len(df_test)

(6090, 2040)

In [ ]:
tf.print(df_train.groupby(target_col.value).count())
tf.print(df_test.groupby(target_col.value).count())

       tweet
label       
0       3199
1       2891
       tweet
label       
0       1071
1        969


# Training 

<font color='blue'>This section is to train and save the model. <br>
__If model is already trained and saved, directly move forward for attack and evaluation section.__ </font>

## BERT Model Training

In [ ]:
pretrained_weights.value

'distilbert-base-uncased'

In [ ]:
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)

In [ ]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')

Alpha: 0.999, Max len : 100, Learning Rate: 2e-05, Batch Size: 4, Ratio: 0.5, Epochs: 3


In [ ]:
bert=bert_model(pretrained_weights.value,max_len.value,learning_rate.value)
bert.summary()

Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'vocab_projector', 'activation_13']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_ids (InputLayer)         [(None, 100)]        0           []                               
                                                                                                  
 attention_mask (InputLayer)    [(None, 100)]        0           []                               
                                                                                                  
 tf_distil_bert_model (TFDistil  TFBaseModelOutput(l  66362880   ['input_ids[0][0]',              
 BertModel)                     ast_hidden_state=(N               'attention_mask[0][0]']         
                                one, 100, 768),                                                   
                                 hidden_states=None                                           

In [ ]:
print(datetime.datetime.now())
with tf.device('/GPU:0'):
    bert.fit(x_train,y_train,batch_size=batch_size.value,epochs=epochs.value,verbose=1)

2021-11-27 10:53:40.537232
Epoch 1/3


KeyboardInterrupt: ignored

In [ ]:
# evaluating model 
pred_label=bert.predict(x_test)

print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

In [ ]:
#saving the model 
if  pretrained_weights.value == 'distilbert-base-uncased':
    bert.save_weights('SavedModels/'+data_name.value+'/DistilBERT_model.h5')
else:
    bert.save_weights('SavedModels/'+data_name.value+'/BERT_model.h5')

## Adversarial Mean Teacher BERT Training

In [ ]:
# Training
tokenizer=create_tokenizer(pretrained_weights.value)
x_train,y_train,vocab_size= data_tokenization(df_train,feature_col.value,target_col.value,max_len.value,tokenizer)
x_test,y_test,_= data_tokenization(df_test,feature_col.value,target_col.value,max_len.value,tokenizer)
x_unlabel,_,_=data_tokenization(df_aug_unlabel,aug_col.value,target_col.value,max_len.value,tokenizer)

In [ ]:
#printing hyperparameters set for training 
print(f'Alpha: {alpha.value}, Max len : {max_len.value}, Learning Rate: {learning_rate.value}, Batch Size: {batch_size.value}, Ratio: {ratio.value}, Epochs: {epochs.value}')


In [ ]:
print(datetime.datetime.now())
# training the model
with tf.device('/GPU:0'):
    student, teacher= train_mean_teacher(x_train, y_train, x_unlabel, 
                                         pretrained_weights.value,
                                         epochs.value,batch_size.value,
                                         learning_rate.value,max_len.value,alpha.value)

In [ ]:
if  pretrained_weights.value == 'distilbert-base-uncased':
    teacher.save_weights('SavedModels/'+data_name.value+'/DistilBERT_teacher.h5')
else:
    teacher.save_weights('SavedModels/'+data_name.value+'/BERT_teacher.h5')


In [ ]:
#evaluating test data 
pred_label=teacher.predict(x_test)

In [ ]:
print(classification_report(np.argmax(y_test,1),np.argmax(pred_label,1)))

# Attack And Evaluation

In [ ]:
import textattack
from Attack_model.TextAttack import attack_model

textattack: Updating TextAttack package dependencies.
textattack: Downloading NLTK required packages.


[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package omw to /root/nltk_data...
[nltk_data]   Unzipping corpora/omw.zip.
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:10<00:00, 44.2MB/s]
textattack: Unzipping file /root/.cache/textattack/tmpamlpkgxf.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.


In [ ]:
# bert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_model.h5',placeholder='Enter Model location ',description=' BERT Model location:',disabled=False)
# MTbert_to_attack=widgets.Textarea(value='SavedModels/Codalab/BERT_teacher.h5',placeholder='Enter Model location ',description=' MTBERT Model location:',disabled=False)   
# pretrained_weights=widgets.Dropdown(options=['bert-base-uncased','distilbert-base-uncased' ],value='bert-base-uncased',description='Pretrained Model:',disabled=False,) 
model_name=widgets.Dropdown(options=['BERT','DistilBERT']
                               ,value='DistilBERT',
                               description='Model Name:',
                               disabled=False,) 
tf.print('\n model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter')
display(model_name)

# tf.print('\n Please select the location of BERT and MT BERT model.\n')
# display(bert_to_attack, MTbert_to_attack)
# tf.print('\n Please select the pretrained model weights.')
# display(pretrained_weights)



 model_name: Model name for attack.Note : Please confirm with the bert_to_attack parameter


Dropdown(description='Model Name:', index=1, options=('BERT', 'DistilBERT'), value='DistilBERT')

In [ ]:
if model_name.value=='BERT':
  bert_to_attack= 'SavedModels/'+data_name.value+'/BERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/BERT_teacher.h5'
  pretrained_weights.value = 'bert-base-uncased'
else:
  bert_to_attack= 'SavedModels/'+data_name.value+'/DistilBERT_model.h5'
  MTbert_to_attack='SavedModels/'+data_name.value+'/DistilBERT_teacher.h5'
  pretrained_weights.value = 'distilbert-base-uncased'
print(model_name.value), bert_to_attack

DistilBERT


(None, 'SavedModels/codalab/DistilBERT_model.h5')

In [ ]:
# attack parameters 

# Query Budget is maximum query allowed
query_budget= widgets.BoundedIntText(value=6000,min=10,max=10000,step=20,description='Query Budget:',disabled=False,)

# number of example to take for attack from test dataset randomly 
num_examples=widgets.BoundedIntText(value=1000,min=10,max=len(df_test),step=20,description='Number of Example:',disabled=False,)

# attack recipes 
attack_recipe=widgets.Dropdown(options=['TextFoolerJin2019',
                                        'PWWSRen2019'
                                        'BAEGarg2019',
                                        'TextBuggerLi2018']
                               ,value='TextFoolerJin2019',
                               description='Attack Recipe:',
                               disabled=False,) 


tf.print('\n query_budget: Maximum Query allowed to attack model')
display(query_budget)
tf.print('\n num_examples: Number of example to take for attack from test dataset randomly. ')
display(num_examples)
# tf.print('\n attack_recipe: Attack methodolgy to attack the model. ')
# display(attack_recipe)



 query_budget: Maximum Query allowed to attack model


BoundedIntText(value=6000, description='Query Budget:', max=10000, min=10, step=20)


 num_examples: Number of example to take for attack from test dataset randomly. 


BoundedIntText(value=1000, description='Number of Example:', max=2040, min=10, step=20)

In [ ]:
'''
Some of the attack recipe provided by textattack is not working with lengthy article. So, 
I am filtering the with the length. May be in future I will remove it.
'''
if not os.path.exists('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv'):
    df_test['len']=df_test.apply(lambda row: len(row[feature_col.value].split()),axis=1)
    print(f'Average length of articles are: {df_test["len"].mean()}')
    # df_test_for_attack= df_test[(df_test['len']>0) & (df_test['len']<100)][[feature_col.value,target_col.value]].dropna().reset_index(drop=True)
    df_test_for_attack=df_test[[feature_col.value,target_col.value]].sample(frac=1).reset_index(drop=True)
    df_test_for_attack= df_test_for_attack[:num_examples.value+1]
    # saving the csv file in AdversarialTestData folder, in order to correctly experiment all recipes with same data
    df_test_for_attack.to_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv',index=False)
else:
    tf.print('Reading the saved file')
    df_test_for_attack= pd.read_csv('Data/'+data_name.value+'/AdversarialTestData/test_adv_'+str(num_examples.value)+'.csv')

print('Length of dataset', len(df_test_for_attack))
df_test_for_attack.head()

Reading the saved file
Length of dataset 1001


tweet  label
0  two member of atletienglish test coronavirus p...      1
1  household should have required medical kit wit...      1
2  a mobile testing unit went to the airport site...      0
3  rt nytscience government across the country ar...      0
4  there are nine people in hospital in auckland ...      0

In [ ]:
df_test_for_attack.groupby(target_col.value).count()

tweet
label       
0        542
1        459

In [ ]:

#creating dataset for the attacking
dataset_for_attack=list(df_test_for_attack.itertuples(index=False, name=None))
dataset_for_attack = textattack.datasets.Dataset(dataset_for_attack)

In [ ]:
# Loading the model
bert= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert.load_weights(bert_to_attack)

bert_teacher= bert_model(pretrained_weights.value,max_len.value,learning_rate.value) 
bert_teacher.load_weights(MTbert_to_attack)

Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'activation_13', 'vocab_projector']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


Model selected: distilbert-base-uncased


Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertModel: ['vocab_layer_norm', 'vocab_transform', 'activation_13', 'vocab_projector']
- This IS expected if you are initializing TFDistilBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
All the layers of TFDistilBertModel were initialized from the model checkpoint at distilbert-base-uncased.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertModel for predictions without further training.


### TextFooler
__TextFoolerJin2019 - Is BERT Really Robust? A Strong Baseline for Natural Language Attack on Text Classification and Entailment.__<br>
In this paper, we present TextFooler, a simple but strong baseline to generate natural adversarial text. By applying it to two fundamental natural language tasks, text classification and textual entailment, we successfully attacked three target models, including the powerful pre-trained BERT, and the widely used convolutional and recurrent neural networks. We demonstrate the advantages of this framework in three ways: (1) effective---it outperforms state-of-the-art attacks in terms of success rate and perturbation rate, (2) utility-preserving---it preserves semantic content and grammaticality, and remains correctly classified by humans, and (3) efficient---it generates adversarial text with computational complexity linear to the text length. *The code, pre-trained target models, and test examples are available at https://github.com/jind11/TextFooler.


In [ ]:
attack_recipe.value= 'TextFoolerJin2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')
tf.print(f'****Attacking model :{model_name.value}*****')

****Attack Recipe:TextFoolerJin2019*****
****Query size:6000*****
****Number of examples:1000*****
****Attacking model :DistilBERT*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextFoolerJin2019/DistilBERT_nexp1000_qb6000_2021-12-02_22:29.csv
  0%|          | 1/1000 [00:00<03:18,  5.03it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       

[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<03:26,  4.84it/s]

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (73%)]] --> [[[SKIPPED]]]

two member of atletienglish test coronavirus positive ahead of ucl quarterfinal not sure how the rest of the team can be on the field in these circumstance championsleague




Using /tmp/tfhub_modules to cache modules.
Downloaded https://tfhub.dev/google/universal-sentence-encoder/4, Total size: 987.47MB
Downloaded TF-Hub Module 'https://tfhub.dev/google/universal-sentence-encoder/4'.
[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:15<2:10:41,  7.86s/it]

...

--------------------------------------------- Result 997 ---------------------------------------------
[[0 (73%)]] --> [[1 (53%)]]

lord loredo james gross yeah california ha been a bear for two reason their [[reporting]] [[ha]] been very irregular until recently they have reported on both side of our daily pm commit they have dropped [[huge]] [[pending]] [[number]] the last day only one of which got captured in our [[daily]] s

lord loredo james gross yeah california ha been a bear for two reason their [[rapport]] [[haya]] been very irregular until recently they have reported on both side of our daily pm commit they have dropped [[hefty]] [[till]] [[numero]] the last day only one of which got captured in our [[unremarkable]] s


--------------------------------------------- Result 998 ---------------------------------------------
[[0 (56%)]] --> [[[SKIPPED]]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but 

[Succeeded / Failed / Skipped / Total] 857 / 82 / 60 / 999: 100%|█████████▉| 999/1000 [15:06<00:00,  1.10it/s]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (72%)]] --> [[1 (64%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[specifics]] whoimpact




[Succeeded / Failed / Skipped / Total] 858 / 82 / 60 / 1000: 100%|██████████| 1000/1000 [15:07<00:00,  1.10it/s]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (73%)]] --> [[1 (51%)]]

a of [[today]] of all the [[sample]] [[tested]] for covid [[have]] been [[positive]] [[currently]] [[bed]] [[isolation]] [[icu]] and [[ventilator]] [[supported]] are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus

a of [[thu]] of all the [[swabs]] [[scrutinized]] for covid [[got]] been [[fruitful]] [[anymore]] [[bassinet]] [[detaching]] [[nicu]] and [[admirer]] [[succour]] are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 858    |
| Number of failed attacks:     | 82     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 94.0%  |
| Ac

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextFoolerJin2019/MTDistilBERT_nexp1000_qb6000_2021-12-02_22:44.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<01:20, 12.35it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.840845057
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
       

[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:04<33:43,  2.03s/it]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (57%)]] --> [[0 (54%)]]

[[household]] should have required medical [[kit]] with certain item and equipment to treat the different stage of covid

[[home]] should have required medical [[toolbox]] with certain item and equipment to treat the different stage of covid




[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:08<45:32,  2.74s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (51%)]] --> [[0 (51%)]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear [[city]] data show death but crematorium burial ground tell a different story theprints soniyaagrawal manishamondal report

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear [[towns]] data show death but crematorium burial ground tell a different story theprints soniyaagrawal manishamondal report




[Succeeded / Failed / Skipped / Total] 599 / 353 / 47 / 999: 100%|█████████▉| 999/1000 [22:52<00:01,  1.37s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (52%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[lucidity]] whoimpact




[Succeeded / Failed / Skipped / Total] 599 / 354 / 47 / 1000: 100%|██████████| 1000/1000 [22:54<00:00,  1.37s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (67%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 599    |
| Number of failed attacks:     | 354    |
| Number of skipped attacks:    | 47     |
| Original accuracy:            | 95.3%  |
| Accuracy under attack:        | 35.4%  |
| Attack success rate:          | 62.85% |
| Average perturbed word %:     | 24.71% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 253.71 |
+-------------------------------+--------+


### TextBugger
__TextBugger: Generating Adversarial Text Against Real-world Applications.__ <br>
Deep Learning-based Text Understanding (DLTU) is the backbone technique behind various applications, including question answering, machine translation, and text classification. Despite its tremendous popularity, the security vulnerabilities of DLTU are still largely unknown, which is highly concerning given its increasing use in security-sensitive applications such as sentiment analysis and toxic content detection. In this paper, we show that DLTU is inherently vulnerable to adversarial text attacks, in which maliciously crafted texts trigger target DLTU systems and services to misbehave. Specifically, we present TextBugger, a general attack framework for generating adversarial texts. In contrast to prior works, TextBugger differs in significant ways: (i) effective -- it outperforms state-of-the-art attacks in terms of attack success rate; (ii) evasive -- it preserves the utility of benign text, with 94.9\% of the adversarial text correctly recognized by human readers; and (iii) efficient -- it generates adversarial text with computational complexity sub-linear to the text length. We empirically evaluate TextBugger on a set of real-world DLTU systems and services used for sentiment analysis and toxic content detection, demonstrating its effectiveness, evasiveness, and efficiency. For instance, TextBugger achieves 100\% success rate on the IMDB dataset based on Amazon AWS Comprehend within 4.61 seconds and preserves 97\% semantic similarity. We further discuss possible defense mechanisms to mitigate such attack and the adversary's potential countermeasures, which leads to promising directions for further research.



In [ ]:
attack_recipe.value= 'TextBuggerLi2018'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:TextBuggerLi2018*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextBuggerLi2018/DistilBERT_nexp1000_qb6000_2021-12-02_23:07.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<01:20, 12.47it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (73%)]] --> [[[SKIPPED]]]

two membe

[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:03<31:20,  1.88s/it]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (59%)]] --> [[0 (53%)]]

household should have required medical [[kit]] with certain item and equipment to treat the different stage of covid

household should have required medical [[package]] with certain item and equipment to treat the different stage of covid




[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:04<26:35,  1.60s/it]

...

--------------------------------------------- Result 997 ---------------------------------------------
[[0 (73%)]] --> [[1 (70%)]]

lord loredo james gross yeah california ha been a bear for two reason their [[reporting]] ha been very irregular until recently they have reported on both side of our daily pm commit they have dropped huge [[pending]] [[number]] the last day only one of which got captured in our [[daily]] s

lord loredo james gross yeah california ha been a bear for two reason their [[repor𝚝ing]] ha been very irregular until recently they have reported on both side of our daily pm commit they have dropped huge [[pendіng]] [[numero]] the last day only one of which got captured in our [[dailies]] s


--------------------------------------------- Result 998 ---------------------------------------------
[[0 (56%)]] --> [[[SKIPPED]]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial 

[Succeeded / Failed / Skipped / Total] 694 / 245 / 60 / 999: 100%|█████████▉| 999/1000 [09:11<00:00,  1.81it/s]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (72%)]] --> [[1 (68%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[particulars]] whoimpact




[Succeeded / Failed / Skipped / Total] 695 / 245 / 60 / 1000: 100%|██████████| 1000/1000 [09:11<00:00,  1.81it/s]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (73%)]] --> [[1 (53%)]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator [[supported]] are vacant in telangana covid   covid  covid  covid [[coronaupdates]] [[coronavirusupdates]] [[coronaviruspandemic]] coronavirus

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator [[backed]] are vacant in telangana covid   covid  covid  covid [[coronaupdateѕ]] [[coronavirսsupdates]] [[coroոaviruspandemic]] coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 695    |
| Number of failed attacks:     | 245    |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 94.0%  |
| Accuracy under attack:        | 24.5%  |
| Attack success rat

#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/TextBuggerLi2018/MTDistilBERT_nexp1000_qb6000_2021-12-02_23:17.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<01:17, 12.93it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  CompositeTransformation(
    (0): WordSwapRandomCharacterInsertion(
        (random_one):  True
      )
    (1): WordSwapRandomCharacterDeletion(
        (random_one):  True
      )
    (2): WordSwapNeighboringCharacterSwap(
        (random_one):  True
      )
    (3): WordSwapHomoglyphSwap
    (4): WordSwapEmbedding(
        (max_candidates):  5
        (embedding):  WordEmbedding
      )
    )
  (constraints): 
    (0): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8
        (window_size):  inf
        (skip_text_shorter_than_window):  False
        (compare_against_original):  True
      )
    (1): RepeatModification
    (2): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (63%)]] --> [[[SKIPPED]]]

two membe

[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:03<31:42,  1.91s/it]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (57%)]] --> [[0 (56%)]]

[[household]] should have required medical [[kit]] with certain item and equipment to treat the different stage of covid

[[home]] should have required medical [[k]] [[it]] with certain item and equipment to treat the different stage of covid




[Succeeded / Failed / Skipped / Total] 1 / 1 / 1 / 3:   0%|          | 3/1000 [00:05<32:49,  1.98s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (51%)]] --> [[0 (56%)]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints [[soniyaagrawal]] manishamondal report

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints [[ѕoniyaagrawal]] manishamondal report




[Succeeded / Failed / Skipped / Total] 412 / 540 / 47 / 999: 100%|█████████▉| 999/1000 [13:07<00:00,  1.27it/s]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (51%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong [[collaboration]] between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong [[collaborating]] between who australia and new zealand more [[detaiⅼ]] whoimpact




[Succeeded / Failed / Skipped / Total] 412 / 541 / 47 / 1000: 100%|██████████| 1000/1000 [13:08<00:00,  1.27it/s]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (67%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 412    |
| Number of failed attacks:     | 541    |
| Number of skipped attacks:    | 47     |
| Original accuracy:            | 95.3%  |
| Accuracy under attack:        | 54.1%  |
| Attack success rate:          | 43.23% |
| Average perturbed word %:     | 24.85% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 97.19  |
+-------------------------------+--------+


### PWWS
__PWWSRen 2019 - Generating Natural Language Adversarial Examples through Probability Weighted Word Saliency. Shuhuai Ren, Yihe Deng, Kun He, Wanxiang Che__<br>
Based on the synonyms substitution strategy, they introduced a new word replacement order determined by both the word saliency and the classification probability, and propose a greedy algorithm called probability weighted word saliency (PWWS) for text adversarial attack.

In [ ]:
attack_recipe.value= 'PWWSRen2019'

# because of issue in PWWS attack provided by textattack I need to change the number of  queries = number of examples
# query_budget.value = 6000
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:PWWSRen2019*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/PWWSRen2019/DistilBERT_nexp1000_qb6000_2021-12-02_23:30.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<01:23, 12.00it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  weighted-saliency
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapWordNet
  (constraints): 
    (0): RepeatModification
    (1): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (73%)]] --> [[[SKIPPED]]]

two member of atletienglish test coronavirus positive ahead of ucl quarterfinal not sure how the rest of the team can be on the field in these circumstance championsleague




[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:00<07:41,  2.16it/s]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (59%)]] --> [[0 (68%)]]

household should have [[required]] medical kit with certain item and equipment to treat the different stage of covid

household should have [[involve]] medical kit with certain item and equipment to treat the different stage of covid




[Succeeded / Failed / Skipped / Total] 2 / 0 / 1 / 3:   0%|          | 3/1000 [00:03<21:22,  1.29s/it]

...

--------------------------------------------- Result 997 ---------------------------------------------
[[0 (73%)]] --> [[1 (66%)]]

lord loredo james gross yeah california ha been a bear for two reason their [[reporting]] ha been very irregular until recently they have reported on both side of our daily [[pm]] commit they have dropped [[huge]] pending [[number]] the last day only one of which [[got]] [[captured]] in our daily s

lord loredo james gross yeah california ha been a bear for two reason their [[describe]] ha been very irregular until recently they have reported on both side of our daily [[promethium]] commit they have dropped [[Brobdingnagian]] pending [[numerate]] the last day only one of which [[dumbfound]] [[enchant]] in our daily s


--------------------------------------------- Result 998 ---------------------------------------------
[[0 (56%)]] --> [[[SKIPPED]]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city d

[Succeeded / Failed / Skipped / Total] 698 / 241 / 60 / 999: 100%|█████████▉| 999/1000 [24:13<00:01,  1.45s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (72%)]] --> [[1 (69%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[contingent]] whoimpact




[Succeeded / Failed / Skipped / Total] 698 / 242 / 60 / 1000: 100%|██████████| 1000/1000 [24:14<00:00,  1.45s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 698    |
| Number of failed attacks:     | 242    |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 94.0%  |
| Accuracy under attack:        | 24.2%  |
| Attack success rate:          | 74.26% |
| Average perturbed word %:     | 19.48% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 212.59 |
+-------------------------------+--------+


#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/PWWSRen2019/MTDistilBERT_nexp1000_qb6000_2021-12-02_23:54.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<01:29, 11.15it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  weighted-saliency
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapWordNet
  (constraints): 
    (0): RepeatModification
    (1): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (63%)]] --> [[[SKIPPED]]]

two member of atletienglish test coronavirus positive ahead of ucl quarterfinal not sure how the rest of the team can be on the field in these circumstance championsleague




[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:01<08:35,  1.94it/s]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (57%)]] --> [[0 (57%)]]

[[household]] should have required medical kit with certain item and equipment to [[treat]] the different stage of covid

[[menage]] should have required medical kit with certain item and equipment to [[process]] the different stage of covid




[Succeeded / Failed / Skipped / Total] 1 / 1 / 1 / 3:   0%|          | 3/1000 [00:05<29:44,  1.79s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (51%)]] --> [[0 (52%)]]

death due to covid have increased in [[gujarats]] rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints soniyaagrawal manishamondal report

death due to covid have increased in [[Gujerat]] rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints soniyaagrawal manishamondal report




[Succeeded / Failed / Skipped / Total] 466 / 486 / 47 / 999: 100%|█████████▉| 999/1000 [27:46<00:01,  1.67s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (51%)]]

papua new guinea now ha the [[supply]] to test for covid in all province thanks to a strong collaboration between who australia and new zealand more detail whoimpact

papua new guinea now ha the [[ply]] to test for covid in all province thanks to a strong collaboration between who australia and new zealand more detail whoimpact




[Succeeded / Failed / Skipped / Total] 466 / 487 / 47 / 1000: 100%|██████████| 1000/1000 [27:47<00:00,  1.67s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (67%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 466    |
| Number of failed attacks:     | 487    |
| Number of skipped attacks:    | 47     |
| Original accuracy:            | 95.3%  |
| Accuracy under attack:        | 48.7%  |
| Attack success rate:          | 48.9%  |
| Average perturbed word %:     | 19.04% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 231.69 |
+-------------------------------+--------+


### BAE
__BAEGarg2019-BAE (BAE: BERT-Based Adversarial Examples)__ <br>
BAE, a black box attack for generating adversarial examples using contextual perturbations from a BERT masked language model. BAE replaces and inserts tokens in the original text by masking a portion of the text and leveraging the BERT-MLM to generate alternatives for the masked tokens. Through automatic and human evaluations, we show that BAE performs a stronger attack, in addition to generating adversarial examples with improved grammaticality and semantic coherence as compared to prior work.


In [ ]:
attack_recipe.value= 'BAEGarg2019'
tf.print(f'****Attack Recipe:{attack_recipe.value}*****')
tf.print(f'****Query size:{query_budget.value}*****')
tf.print(f'****Number of examples:{num_examples.value}*****')

****Attack Recipe:BAEGarg2019*****
****Query size:6000*****
****Number of examples:1000*****


#### BERT

In [ ]:
attack_model(bert, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/BAEGarg2019/DistilBERT_nexp1000_qb6000_2021-12-03_07:01.csv
[Succeeded / Failed / Skipped / Total] 0 / 0 / 1 / 1:   0%|          | 1/1000 [00:00<02:10,  7.68it/s]

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapMaskedLM(
    (method):  bae
    (masked_lm_name):  BertForMaskedLM
    (max_length):  512
    (max_candidates):  50
    (min_confidence):  0.0
  )
  (constraints): 
    (0): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (1): UniversalSentenceEncoder(
        (metric):  cosine
        (threshold):  0.936338023
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  True
      )
    (2): RepeatModification
    (3): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (73%)]] --> [[[SKIPPED]]]

two member of atletienglish test coronavirus positive ahead of ucl quarterfina

Using /tmp/tfhub_modules to cache modules.
Downloaded https://tfhub.dev/google/universal-sentence-encoder/4, Total size: 987.47MB
Downloaded TF-Hub Module 'https://tfhub.dev/google/universal-sentence-encoder/4'.
[Succeeded / Failed / Skipped / Total] 1 / 0 / 1 / 2:   0%|          | 2/1000 [00:16<2:13:11,  8.01s/it]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (59%)]] --> [[0 (60%)]]

household should have required [[medical]] kit with certain item and equipment to treat the different stage of covid

household should have required [[care]] kit with certain item and equipment to treat the different stage of covid




...

--------------------------------------------- Result 997 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

lord loredo james gross yeah california ha been a bear for two reason their reporting ha been very irregular until recently they have reported on both side of our daily pm commit they have dropped huge pending number the last day only one of which got captured in our daily s


--------------------------------------------- Result 998 ---------------------------------------------
[[0 (56%)]] --> [[[SKIPPED]]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints soniyaagrawal manishamondal report




[Succeeded / Failed / Skipped / Total] 264 / 675 / 60 / 999: 100%|█████████▉| 999/1000 [33:36<00:02,  2.02s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (72%)]] --> [[1 (58%)]]

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[detail]] whoimpact

papua new guinea now ha the supply to test for covid in all province thanks to a strong collaboration between who australia and new zealand more [[towards]] whoimpact




[Succeeded / Failed / Skipped / Total] 264 / 676 / 60 / 1000: 100%|██████████| 1000/1000 [33:39<00:00,  2.02s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (73%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 264    |
| Number of failed attacks:     | 676    |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 94.0%  |
| Accuracy under attack:        | 67.6%  |
| Attack success rate:          | 28.09% |
| Average perturbed word %:     | 19.31% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 78.25  |
+-------------------------------+--------+


#### MT BERT

In [ ]:
attack_model(bert_teacher, 
             dataset_for_attack,
             data_name.value,
             pretrained_weights.value,
             max_len.value,
             'MT'+model_name.value,
             attack_recipe=attack_recipe.value,
             query_budget= query_budget.value,
             num_examples=num_examples.value)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
textattack: Unknown if model of class <class 'keras.engine.functional.Functional'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path Result/codalab/BAEGarg2019/MTDistilBERT_nexp1000_qb6000_2021-12-03_07:35.csv
[Succeeded / Failed / Skipped / Total] 

Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapMaskedLM(
    (method):  bae
    (masked_lm_name):  BertForMaskedLM
    (max_length):  512
    (max_candidates):  50
    (min_confidence):  0.0
  )
  (constraints): 
    (0): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (1): UniversalSentenceEncoder(
        (metric):  cosine
        (threshold):  0.936338023
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  True
      )
    (2): RepeatModification
    (3): StopwordModification
  (is_black_box):  True
) 

--------------------------------------------- Result 1 ---------------------------------------------
[[0 (63%)]] --> [[[SKIPPED]]]

two member of atletienglish test coronavirus positive ahead of ucl quarterfina

[Succeeded / Failed / Skipped / Total] 0 / 1 / 1 / 2:   0%|          | 2/1000 [00:05<45:08,  2.71s/it]

--------------------------------------------- Result 2 ---------------------------------------------
[[1 (57%)]] --> [[[FAILED]]]

household should have required medical kit with certain item and equipment to treat the different stage of covid




[Succeeded / Failed / Skipped / Total] 0 / 2 / 1 / 3:   0%|          | 3/1000 [00:09<50:52,  3.06s/it]

...

--------------------------------------------- Result 998 ---------------------------------------------
[[1 (51%)]] --> [[0 (61%)]]

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints [[soniyaagrawal]] manishamondal report

death due to covid have increased in gujarats rajkot a case rise however the exact number is unclear city data show death but crematorium burial ground tell a different story theprints [[find]] manishamondal report




[Succeeded / Failed / Skipped / Total] 210 / 742 / 47 / 999: 100%|█████████▉| 999/1000 [33:53<00:02,  2.04s/it]

--------------------------------------------- Result 999 ---------------------------------------------
[[0 (61%)]] --> [[1 (51%)]]

papua new guinea now [[ha]] the supply to test for covid in all province thanks to a strong [[collaboration]] between who australia and new zealand more [[detail]] whoimpact

papua new guinea now [[requires]] the supply to test for covid in all province thanks to a strong [[cooperation]] between who australia and new zealand more [[towards]] whoimpact




[Succeeded / Failed / Skipped / Total] 210 / 743 / 47 / 1000: 100%|██████████| 1000/1000 [33:56<00:00,  2.04s/it]

--------------------------------------------- Result 1000 ---------------------------------------------
[[0 (67%)]] --> [[[FAILED]]]

a of today of all the sample tested for covid have been positive currently bed isolation icu and ventilator supported are vacant in telangana covid   covid  covid  covid coronaupdates coronavirusupdates coronaviruspandemic coronavirus



+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 210    |
| Number of failed attacks:     | 743    |
| Number of skipped attacks:    | 47     |
| Original accuracy:            | 95.3%  |
| Accuracy under attack:        | 74.3%  |
| Attack success rate:          | 22.04% |
| Average perturbed word %:     | 20.52% |
| Average num. words per input: | 25.4   |
| Avg num queries:              | 86.21  |
+-------------------------------+--------+
